<div align="center">
  <h2>Basic recommender system</h2>
</div>




We try to build a basic recommender system using the singular value
decomposition technique SVD. MovieLens 100K is a public dataset that has
943 users, 1683 movies, and around 100K ratings given by users to movers in
a range of 1 to 5. Each rating is associated with a timestamp as shown in the
next sample. <br>

 *Table 1 Example of MovieLens dataset structure with 2 users and 3 movies.*
|User_id |Movie_id | Rating | Timestamp|
|--------|---------|--------|----------|
|1       |1        |       4| 455664   |
|1       |2        |1       |455555    |
|2       |2        |4       |444555    |
|2       |3        |2       |555554    |


A main challenge in building a reliable recommender system is data sparsity,
which represents the portion of missing values that limits the performances of
any statistical technique. The previous table can be turned into 2D table ($i.e.$,
rows represents users, columns represents movies.) to show the sparsity of
data, where $X$ represents a missing value or a target value that we like to
predict.

*Table 2 Structure of dense table with missing values.*

|1  | 2 |3  |
|---|---|---|
|4  |1  |X  |
|X  |4  |2  |

The application of SVD on MovieLens 100k generates three matrixes $U, S,$
and $V$. Where, $U$ represents a matrix of $|U|$ vector represents the hidden
preferences of a given user u from $U$ to the set of movies. Similarly, $V$
represents a matrix of $|V|$ vectors each of which explains how a given movie $v$
from $M$ is liked by users.

To apply and test SVD:
1. Load MovieLens 100k <b>data</b>, and omit timestamp column. Data takes
the form lines, separated by a token ($i.e.$, comma, or a tabular.) such
as a CSV file.
2. Split the<b> data</b> into <b>train</b> and <b>test</b> parts by considering $80\%$ and $20\%$
for the splits respectively.
3. Convert the <b>train</b>, and <b>test</b> into dense tables named <b>training_data</b>,
and <b>testing_data</b> ($i.e.$, as in the previous example, we pass from table
1 to table 2).
4. Calculate the <b>global_mean</b> of all ratings in the training data.
5. Fix the next controlling parameters: <br>
-  <b>Lamb:</b> a normalization parameter that we set equal to $0.99$.
6. Calculate the users’ bias $b_u$ of each user $u$ calculated as:
$$
 b_u = \frac{\sum_{i \in I_u} (\text{rating}(u, i) - \text{global\_mean})}{\text{lamb} + |I_u|}
$$
Where $I_u$ is the set of items rated by $u$



|Ratings        | Users’ Bias |
|---------------|------       |
|1 2 3         | ?           |
|4 1 X          | ?           |
|X 4 2          |?            |


7. Calculate the bias $b_i$ of each item calculated as:
$$
 b_i = \frac{\sum_{i \in U_i} (\text{rating}(u, i) - \text{global\_mean})}{\text{lamb} + |U_i|}
$$

8. Fill the missing values of the <b> traing_data </b> using the formula:
$$
\text{missing}(u,i) = b_u + b_i + global\_mean
$$

|1 |2 | 3|
|--|--|--|
|4 |1 |? |
|? |4 |2 |

9. Apply SVD on the <b>training_data<b/> and get $U, S, V.$ <br>
$(U,S,V) = SVD(training\_data) $

-  $U$ = $U$[:, <b>Approx</b>.]
-  $V$ = $V$[<b>Approx</b>, :]
-  $S$ = $S$[<b>Approx</b>; <b>Approx</b>]

10. Reduce $U, S, V$ to keep only <b> Approx </b> column for U, and V, and
<b>Approx</b> columns and row for S.

    11. Calculate<b> $Z$</b> as:
    $$Z = U.S.V$$

    12. Calculate the MAE of the model using the next formula:
    $$
    MAE =  \sum_{(u, i) \in (U, I)} |\text{testing\_data}(u,i) - Z(u,i) |
    $$
    Where $ \text{testing\_data}(u,i) \neq 0 $

    13. Redo the steps 9 to 12 by setting <b>Approx</b> equal to
    $[5,10,15,20,25,30,35,40,45,50]$
    14. Plot a bar graph representing the <b>MAE </b>for each configuration.

In [97]:
import pandas as pd
import numpy as np
df = pd.read_csv('dataset/users_and_ratings.csv')
print(df.to_string(index=False))

 user_id  movie_id  rating  timestamp
     196       242       3  881250949
     186       302       3  891717742
      22       377       1  878887116
     244        51       2  880606923
     166       346       1  886397596
     298       474       4  884182806
     115       265       2  881171488
     253       465       5  891628467
     305       451       3  886324817
       6        86       3  883603013
      62       257       2  879372434
     286      1014       5  879781125
     200       222       5  876042340
     210        40       3  891035994
     224        29       3  888104457
     303       785       3  879485318
     122       387       5  879270459
     194       274       2  879539794
     291      1042       4  874834944
     234      1184       2  892079237
     119       392       4  886176814
     167       486       4  892738452
     299       144       4  877881320
     291       118       2  874833878
     308         1       4  887736532
      95    

In [98]:
df

user_id  movie_id  rating  timestamp
0          196       242       3  881250949
1          186       302       3  891717742
2           22       377       1  878887116
3          244        51       2  880606923
4          166       346       1  886397596
...        ...       ...     ...        ...
99995      880       476       3  880175444
99996      716       204       5  879795543
99997      276      1090       1  874795795
99998       13       225       2  882399156
99999       12       203       3  879959583

[100000 rows x 4 columns]

In [99]:
from sklearn.model_selection import train_test_split
train, test = train_test_split(df, test_size=0.2, random_state=42)

Converting the train and test data into dense tables refers to reshaping the data into a matrix-like structure where rows represent users, columns represent movies, and the matrix cells contain the ratings given by users to movies. The term "dense table" implies that there are no missing values in the table, and every user-movie pair has a corresponding rating.


| User_id | Movie_id | Rating |
|---------|----------|--------|
|    1    |    1     |   4    |
|    1    |    2     |   1    |
|    2    |    2     |   4    |
|    2    |    3     |   2    |


<br>

|     | 1 | 2 | 3 |
|-----|---|---|---|
|  1  | 4 | 1 | X |
|  2  | X | 4 | 2 |


Each pair of $(i=UserId , j=MovieId) $ corresponds to a movie rating


Why do we need to turn it intro a sparse matrix ? 
SVD and other matrix factorization techniques work with matrices where rows represent users, columns represent items (movies in this case), and matrix entries contain the ratings given by users to items. This structure is inherent in a dense table, making it suitable for these techniques.

In [100]:
df.columns

Index(['user_id', 'movie_id', 'rating', 'timestamp'], dtype='object')

In [101]:
training_data_dense = train.pivot(index='user_id', columns='movie_id', values='rating')
testing_data_dense = test.pivot(index='user_id', columns='movie_id', values='rating')

In [102]:
training_data_dense

movie_id  1     2     3     4     5     6     7     8     9     10    ...  \
user_id                                                               ...   
1          NaN   3.0   4.0   NaN   3.0   NaN   4.0   NaN   5.0   3.0  ...   
2          4.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
3          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
4          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
5          4.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
939        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   5.0   NaN  ...   
940        NaN   NaN   NaN   2.0   NaN   NaN   NaN   NaN   3.0   NaN  ...   
941        5.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
942        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
943        NaN   5.0   NaN   NaN   NaN   NaN   NaN   NaN   3.0   NaN  ...   

movie_id  1668  1670  1671  1672  1673  1676  1678  1679  1680  1681  
user_id                                                               
1          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
2          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
3          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
4          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
5          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
939        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
940        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
941        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
942        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
943        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  

[943 rows x 1653 columns]

### NOTE :
 We can achieve the same results by using the unstack() function and selecting the column rating to be the intersection of the user_id and the movie_id (Like we have seen in TP6)

In [103]:
training_data_dense2 = train.set_index(['user_id', 'movie_id']).unstack(fill_value=None)['rating']
testing_data_dense2 = test.set_index(['user_id', 'movie_id']).unstack(fill_value=None)['rating']

In [104]:
training_data_dense2

movie_id  1     2     3     4     5     6     7     8     9     10    ...  \
user_id                                                               ...   
1          NaN   3.0   4.0   NaN   3.0   NaN   4.0   NaN   5.0   3.0  ...   
2          4.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
3          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
4          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
5          4.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
939        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   5.0   NaN  ...   
940        NaN   NaN   NaN   2.0   NaN   NaN   NaN   NaN   3.0   NaN  ...   
941        5.0   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
942        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  ...   
943        NaN   5.0   NaN   NaN   NaN   NaN   NaN   NaN   3.0   NaN  ...   

movie_id  1668  1670  1671  1672  1673  1676  1678  1679  1680  1681  
user_id                                                               
1          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
2          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
3          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
4          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
5          NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  
939        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
940        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
941        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
942        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  
943        NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN   NaN  

[943 rows x 1653 columns]

In [105]:
global_mean = training_data_dense.stack().mean()
global_mean

3.5312625

In [106]:
lamb = 0.99

In [107]:
# Calculate users' bias
bu = training_data_dense.apply(lambda row: (row - global_mean).sum() / (lamb + row.count()), axis=1)

bu

user_id
1      0.155497
2      0.267332
3     -0.715521
4      0.923047
5     -0.664179
         ...   
939    0.808130
940   -0.103149
941    0.665288
942    0.719320
943   -0.136118
Length: 943, dtype: float64

In [108]:
#  Calculate items' bias (movies' bias)
bi = training_data_dense.apply(lambda col: (col - global_mean).sum() / (lamb + col.count()))
bi

movie_id
1       0.333122
2      -0.324262
3      -0.423734
4       0.017769
5      -0.280856
          ...   
1676   -0.769479
1678   -1.271991
1679   -0.266966
1680   -0.769479
1681   -0.266966
Length: 1653, dtype: float64

In [109]:
# Fill the NaN values in the training data with the bias values
training_data_filled = bu.values[:, np.newaxis] + bi.values[np.newaxis, :] + global_mean
filled_df_mat = pd.DataFrame(training_data_filled, index=training_data_dense.index, columns=training_data_dense.columns)
filled_df_mat

movie_id      1         2         3         4         5         6     \
user_id                                                                
1         4.019882  3.362498  3.263026  3.704529  3.405904  3.796184   
2         4.131716  3.474332  3.374861  3.816363  3.517738  3.908018   
3         3.148864  2.491479  2.392008  2.833510  2.534885  2.925165   
4         4.787431  4.130047  4.030576  4.472078  4.173453  4.563733   
5         3.200206  2.542821  2.443350  2.884852  2.586228  2.976508   
...            ...       ...       ...       ...       ...       ...   
939       4.672515  4.015130  3.915659  4.357161  4.058536  4.448816   
940       3.761236  3.103851  3.004380  3.445882  3.147258  3.537538   
941       4.529673  3.872289  3.772817  4.214320  3.915695  4.305975   
942       4.583705  3.926320  3.826849  4.268351  3.969727  4.360007   
943       3.728266  3.070882  2.971411  3.412913  3.114288  3.504568   

movie_id      7         8         9         10    ...      1668      1670  \
user_id                                           ...                       
1         3.966541  4.089227  4.061893  4.042628  ...  3.419794  3.419794   
2         4.078376  4.201062  4.173728  4.154463  ...  3.531628  3.531628   
3         3.095523  3.218209  3.190875  3.171610  ...  2.548775  2.548775   
4         4.734091  4.856777  4.829443  4.810178  ...  4.187343  4.187343   
5         3.146865  3.269551  3.242217  3.222952  ...  2.600118  2.600118   
...            ...       ...       ...       ...  ...       ...       ...   
939       4.619174  4.741860  4.714526  4.695261  ...  4.072426  4.072426   
940       3.707895  3.830581  3.803247  3.783982  ...  3.161148  3.161148   
941       4.476332  4.599018  4.571684  4.552419  ...  3.929585  3.929585   
942       4.530364  4.653050  4.625716  4.606451  ...  3.983617  3.983617   
943       3.674926  3.797612  3.770278  3.751013  ...  3.128178  3.128178   

movie_id      1671      1672      1673      1676      1678      1679  \
user_id                                                                
1         2.414769  2.662504  3.419794  2.917281  2.414769  3.419794   
2         2.526603  2.774339  3.531628  3.029116  2.526603  3.531628   
3         1.543750  1.791486  2.548775  2.046263  1.543750  2.548775   
4         3.182318  3.430053  4.187343  3.684831  3.182318  4.187343   
5         1.595092  1.842828  2.600118  2.097605  1.595092  2.600118   
...            ...       ...       ...       ...       ...       ...   
939       3.067401  3.315137  4.072426  3.569914  3.067401  4.072426   
940       2.156122  2.403858  3.161148  2.658635  2.156122  3.161148   
941       2.924560  3.172295  3.929585  3.427072  2.924560  3.929585   
942       2.978591  3.226327  3.983617  3.481104  2.978591  3.983617   
943       2.123153  2.370888  3.128178  2.625666  2.123153  3.128178   

movie_id      1680      1681  
user_id                       
1         2.917281  3.419794  
2         3.029116  3.531628  
3         2.046263  2.548775  
4         3.684831  4.187343  
5         2.097605  2.600118  
...            ...       ...  
939       3.569914  4.072426  
940       2.658635  3.161148  
941       3.427072  3.929585  
942       3.481104  3.983617  
943       2.625666  3.128178  

[943 rows x 1653 columns]

In [110]:
# Apply SVD on training_data
U, S, V = np.linalg.svd(training_data_filled, full_matrices=False)



In [111]:
# Reduce U, S, V
approx = 10  # number of columns and rows to keep
U = U[:, :approx]
V = V[:approx, :]
S = np.diag(S[:approx])

In [114]:
Z = np.dot(np.dot(U, S), V)
Z.shape

(943, 1653)